## DSPy MIPRO optimized for ReAct Agent with Weaviate Query Agent Tool

This notebook illustrates how MIPROv2 with `medium` intensity improves the performance of a ReAct Agent using the Weaviate Query Agent as a tool from 440 to 470 (out of 500) on Weaviate support questions!

**IMPORTANT!** Please note this currently mocks the Query Agent Tool as shown below to speed this up. Stay tuned for more content about DSPy MIPRO <> Weaviate Query Agent optimization!

### Requirements
1. Weaviate Cloud instance (WCD): The Weaviate Query Agent is only accessible through WCD at the moment. You can create a serverless cluster or a free 14-day sandbox [here](https://console.weaviate.cloud/).
1. Install DSPy with `pip install -U dspy`
1. Install the Weaviate Agents package with `pip install weaviate-agents`
1. You'll need a Weaviate cluster with data. If you don't have one, check out [this notebook](integrations/Weaviate-Import-Example.ipynb) to import the Weaviate Blogs.

### Import libraries and keys

In [ ]:
import weaviate
from weaviate_agents.query import QueryAgent
import os
import logging

import dspy
from dspy.evaluate.evaluate import Evaluate

In [ ]:
os.environ["WEAVIATE_URL"] = ""
os.environ["WEAVIATE_API_KEY"] = ""
os.environ["OPENAI_API_KEY"] = ""

### Define function (mock example)

In [2]:
def query_agent_request(query: str) -> str:
    """
    Send a query to the database and get the response.

    Args:
        query (str): The question or query to search for in the database. This can be any natural language question related to the content stored in the database.

    Returns:
        str: The response from the database containing relevant information.
    """
    return """Etienne Dilocker 2021 -- Why does Weaviate use Docker & Docker-Compose?
There are many arguments for or against containerization, we have decided to go with Docker & Docker-Compose in the Weaviate stack for the following reasons:

Portability: Whether you're running on Windows, Linux, macOS or yet another OS, Weaviate is only compiled for a single Linux distribution. The Docker container makes sure that from Weaviate's perspective it's always running on a well-known Linux — even if your Host machine is running a completely different OS.
Isolation & Predictability: Weaviate is a compiled binary that has zero runtime dependencies, but if you use Weaviate modules which rely on third-party tools, such as Huggingface Transformers, PyTorch or Tensorflow, they have a set of runtime dependencies. Thanks to containers, all runtime dependencies (Python version, python packages, OS libraries, etc.) are guaranteed to be present and at the right version in each container.
Distribution via Docker Hub: Docker Hub makes it very easy to distribute public images. With a single docker pull semitechnologies/weaviate:latest command you can always obtain the latest version — without any prior configuration. Additionally, each container can have an exact version number, making it easy to switch between versions or upgrade your setup. Instead of a lengthy and risky update process, you can simply exchange the entire container for that of a newer version."""

In [5]:
# Only show warnings and errors from LiteLLM
logging.getLogger("LiteLLM").setLevel(logging.WARNING)


### Configure LLM

In [ ]:
lm = dspy.LM('openai/gpt-4o-mini', api_key=os.getenv('OPENAI_API_KEY'))
dspy.configure(lm=lm)

### Create agents

In [6]:
query_agent_init_prompt = "Use the database querying tool to answer the user questions."
llm_as_judge_prompt = "Rate the system's answer to the user's question on a scale of 1 to 5 with 1 being terrible and 5 being incredible!"
react_with_query_agent_signature = dspy.Signature("user_question: str -> helpful_response: str", query_agent_init_prompt)
llm_as_judge_signature = dspy.Signature("user_question: str, system_response: str -> response_rating: float", llm_as_judge_prompt)
react_with_query_agent = dspy.ReAct(react_with_query_agent_signature, tools=[query_agent_request], max_iters=2)
llm_as_judge = dspy.Predict(llm_as_judge_signature)

In [7]:
user_question = "What does Docker do?"
react_answer = react_with_query_agent.forward(user_question = user_question).helpful_response
print(react_answer)
llm_as_judge_rating = llm_as_judge.forward(user_question = user_question,
                                           system_response = react_answer).response_rating
print(llm_as_judge_rating)

Docker is a platform that allows developers to automate the deployment of applications inside lightweight, portable containers. It provides benefits such as portability across different operating systems, isolation of application dependencies, and easy distribution of application images.
5.0


In [8]:
def llm_as_judge_rating(gold, pred, trace=None):
    return llm_as_judge.forward(user_question=gold.user_question,
                               system_response=pred.helpful_response).response_rating

In [21]:
data = []
questions = [
    "Why does Weaviate use containerization for its stack?",
    "How does Docker help Weaviate overcome operating system compatibility issues?",
    "What advantage does Docker provide when Weaviate modules rely on third-party tools?",
    "How does Docker Hub benefit Weaviate's distribution process?",
    "What makes version management and upgrades easier with Docker containers according to the blurb?",
    "What are the key benefits of using Docker containers for Weaviate deployment?",
    "How does Docker ensure consistent runtime environments for Weaviate?",
    "What role does containerization play in Weaviate's cross-platform compatibility?",
    "How does Docker simplify the management of Weaviate's dependencies?",
    "What are the advantages of using Docker Hub for Weaviate distribution?",
    "How does Docker containerization affect Weaviate's portability across different platforms?",
    "What benefits does Docker provide for managing Weaviate's third-party integrations?",
    "How does Docker help maintain consistency in Weaviate's runtime environment?",
    "What makes Docker an effective solution for Weaviate's distribution needs?",
    "How does containerization improve Weaviate's deployment process?"
]

for question in questions:
    data.append(dspy.Example(user_question=question).with_inputs("user_question"))

trainset, testset = data[:10], data[10:]

In [22]:
evaluate = Evaluate(devset=testset, num_threads=4, display_progress=False, display_table=True)

uncompiled_score = evaluate(react_with_query_agent, metric=llm_as_judge_rating)

2025/03/05 18:35:46 INFO dspy.evaluate.evaluate: Average Metric: 22.0 / 5 (440.0%)


user_question  \
0  How does Docker containerization affect Weaviate's portability acr...   
1  What benefits does Docker provide for managing Weaviate's third-pa...   
2  How does Docker help maintain consistency in Weaviate's runtime en...   
3  What makes Docker an effective solution for Weaviate's distributio...   
4       How does containerization improve Weaviate's deployment process?   

                                                              trajectory  \
0  {'thought_0': "I need to gather information about how Docker conta...   
1  {'thought_0': "I need to find information about the benefits of us...   
2  {'thought_0': "I need to query the database to find information on...   
3  {'thought_0': "I need to gather information about Docker and its e...   
4  {'thought_0': "I need to query the database to find information on...   

                                                               reasoning  \
0  Docker containerization significantly enhances Weaviate's portabil...   
1  Docker provides several benefits for managing Weaviate's third-par...   
2  Docker helps maintain consistency in Weaviate's runtime environmen...   
3  Docker is an effective solution for Weaviate's distribution needs ...   
4  Containerization improves Weaviate's deployment process by offerin...   

                                                        helpful_response  \
0  Docker containerization greatly improves Weaviate's portability by...   
1  Docker offers significant advantages for managing Weaviate's third...   
2  Docker maintains consistency in Weaviate's runtime environment by ...   
3  Docker is an effective solution for Weaviate's distribution needs ...   
4  Containerization enhances Weaviate's deployment process by ensurin...   

  llm_as_judge_rating  
0          ✔️ [5.000]  
1          ✔️ [4.000]  
2          ✔️ [4.000]  
3          ✔️ [4.500]  
4          ✔️ [4.500]

### MIPRO Optimizer

In [23]:
tp = dspy.MIPROv2(metric=llm_as_judge_rating, auto="medium", num_threads=1, verbose=False)
optimized_react = tp.compile(react_with_query_agent, trainset=trainset)

2025/03/05 18:35:54 INFO dspy.teleprompt.mipro_optimizer_v2: 
RUNNING WITH THE FOLLOWING MEDIUM AUTO RUN SETTINGS:
num_trials: 25
minibatch: False
num_candidates: 9
valset size: 8

2025/03/05 18:35:57 INFO dspy.teleprompt.mipro_optimizer_v2: 
==> STEP 1: BOOTSTRAP FEWSHOT EXAMPLES <==
2025/03/05 18:35:57 INFO dspy.teleprompt.mipro_optimizer_v2: These will be used as few-shot example candidates for our program and for creating instructions.

2025/03/05 18:35:57 INFO dspy.teleprompt.mipro_optimizer_v2: Bootstrapping N=9 sets of demonstrations...


Bootstrapping set 1/9
Bootstrapping set 2/9
Bootstrapping set 3/9


100%|██████████| 2/2 [00:00<00:00, 93.70it/s]


Bootstrapped 2 full traces after 1 examples for up to 1 rounds, amounting to 2 attempts.
Bootstrapping set 4/9


 50%|█████     | 1/2 [00:00<00:00, 114.80it/s]


...

request_id: req_d969f37cc11343484e80d73e5bc47a7e


Average Metric: 34.00 / 8 (425.0%): 100%|██████████| 8/8 [00:25<00:00,  3.19s/it]

2025/03/05 18:55:17 INFO dspy.evaluate.evaluate: Average Metric: 34.0 / 8 (425.0%)
2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: Score: 425.0 with parameters ['Predictor 0: Instruction 0', 'Predictor 0: Few-Shot Set 1', 'Predictor 1: Instruction 0', 'Predictor 1: Few-Shot Set 8'].
2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: Scores so far: [437.5, 456.25, 468.75, 431.25, 431.25, 431.25, 437.5, 406.25, 450.0, 437.5, 462.5, 462.5, 443.75, 450.0, 456.25, 412.5, 437.5, 468.75, 462.5, 456.25, 437.5, 468.75, 456.25, 437.5, 425.0]
2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: Best score so far: 468.75
2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: =========================


2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: ===== Trial 25 / 25 =====



Average Metric: 37.50 / 8 (468.8%): 100%|██████████| 8/8 [00:00<00:00, 102.99it/s]

2025/03/05 18:55:17 INFO dspy.evaluate.evaluate: Average Metric: 37.5 / 8 (468.8%)
2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: Score: 468.75 with parameters ['Predictor 0: Instruction 0', 'Predictor 0: Few-Shot Set 0', 'Predictor 1: Instruction 4', 'Predictor 1: Few-Shot Set 8'].
2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: Scores so far: [437.5, 456.25, 468.75, 431.25, 431.25, 431.25, 437.5, 406.25, 450.0, 437.5, 462.5, 462.5, 443.75, 450.0, 456.25, 412.5, 437.5, 468.75, 462.5, 456.25, 437.5, 468.75, 456.25, 437.5, 425.0, 468.75]
2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: Best score so far: 468.75
2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: =========================


2025/03/05 18:55:17 INFO dspy.teleprompt.mipro_optimizer_v2: Returning best identified program with score 468.75!


In [24]:
optimized_react_answer = optimized_react.forward(user_question = user_question).helpful_response
print(optimized_react_answer)

Docker is a platform that automates the deployment of applications within lightweight, portable containers. These containers package the application code along with its dependencies, ensuring that the application runs consistently across different environments. Key benefits of using Docker include:

1. **Portability**: Docker containers can run on any operating system that supports Docker, making it easy to deploy applications across different environments.
2. **Isolation**: Each container runs in its own environment, ensuring that dependencies and configurations do not conflict with other applications.
3. **Ease of Distribution**: Docker Hub allows for easy sharing and distribution of container images, enabling quick updates and version management.

Overall, Docker enhances deployment efficiency and system reliability by providing a consistent and isolated environment for applications.


In [25]:
lm.inspect_history(n=1)





[2025-03-05T18:55:26.320415]

System message:

Your input fields are:
1. `user_question` (str)
2. `trajectory` (str)

Your output fields are:
1. `reasoning` (str)
2. `helpful_response` (str)

All interactions will be structured in the following way, with the appropriate values filled in.

[[ ## user_question ## ]]
{user_question}

[[ ## trajectory ## ]]
{trajectory}

[[ ## reasoning ## ]]
{reasoning}

[[ ## helpful_response ## ]]
{helpful_response}

[[ ## completed ## ]]

In adhering to this structure, your objective is: 
        Leverage the database querying tool to provide comprehensive answers to user inquiries about Weaviate's architecture, especially focusing on the role of Docker and containerization in enhancing deployment efficiency and system reliability. Start by analyzing the user's question, formulate a clear thought process to identify the necessary database query, and then retrieve relevant information to construct a well-rounded response.


User message:

[[ ## user

In [26]:
compiled_score = evaluate(optimized_react, metric=llm_as_judge_rating)
print(compiled_score)

2025/03/05 18:55:38 INFO dspy.evaluate.evaluate: Average Metric: 23.5 / 5 (470.0%)


user_question  \
0  How does Docker containerization affect Weaviate's portability acr...   
1  What benefits does Docker provide for managing Weaviate's third-pa...   
2  How does Docker help maintain consistency in Weaviate's runtime en...   
3  What makes Docker an effective solution for Weaviate's distributio...   
4       How does containerization improve Weaviate's deployment process?   

                                                              trajectory  \
0  {'thought_0': "Docker containerization enhances Weaviate's portabi...   
1  {'thought_0': "Docker provides several benefits for managing Weavi...   
2  {'thought_0': "Docker helps maintain consistency in Weaviate's run...   
3  {'thought_0': "Docker is effective for Weaviate's distribution nee...   
4  {'thought_0': "Containerization improves Weaviate's deployment pro...   

                                                               reasoning  \
0  Docker containerization significantly enhances Weaviate's portabil...   
1  Docker enhances the management of Weaviate's third-party integrati...   
2  Docker helps maintain consistency in Weaviate's runtime environmen...   
3  Docker is an effective solution for Weaviate's distribution needs ...   
4  Containerization significantly enhances Weaviate's deployment proc...   

                                                        helpful_response  \
0  Docker containerization greatly improves Weaviate's portability by...   
1  Docker offers several key benefits for managing Weaviate's third-p...   
2  Docker enhances the consistency of Weaviate's runtime environment ...   
3  Docker enhances Weaviate's distribution capabilities by offering s...   
4  Containerization improves Weaviate's deployment process in several...   

  llm_as_judge_rating  
0          ✔️ [5.000]  
1          ✔️ [4.500]  
2          ✔️ [5.000]  
3          ✔️ [4.500]  
4          ✔️ [4.500]

470.0
